In [1]:
from transformers import T5Tokenizer, T5ForConditionalGeneration
from transformers import AutoModel, AutoTokenizer
from transformers import MarianMTModel
from transformers import XLMRobertaForSequenceClassification


import os
import pandas as pd
from tqdm import tqdm

tqdm.pandas()

In [2]:
def detect_language(model, tokenizer, text):
    
    token_dict = tokenizer(text, return_tensors="pt").to("cuda")
    outputs = model(token_dict.input_ids)
    decoded = outputs.logits.argmax(-1).item()
    lang = model.config.id2label[decoded]
    return lang

def translate(model, tokenizer, text):
    input_ids = tokenizer(text, return_tensors="pt").input_ids.to("cuda")
    outputs = model.generate(input_ids)
    decoded = tokenizer.decode(outputs[0], skip_special_tokens=True)
    return decoded

In [24]:
DATASET_PATH = "../data/processed/"

df = pd.read_csv(DATASET_PATH, index_col=[0])
df

text  label
INDEX                                                          
0      Maybe the UN could talk to those asian and afr...      1
1      ‘Juice (Jews) are worse that nukes.’ Caption t...      1
2      Foreigners on UK benefits leaps 41% in 5 years...      1
3      Jews cannot be patriots, since their allegianc...      1
4      Israel, Zionism and Jewish Supremacist control...      1
...                                                  ...    ...
4998                      Woman are basically childlike.      1
4999                  women should be submissive to men.      1
5000   Women are essentially childlike, unable to und...      1
5001                  Women should be submissive to men.      1
5002   Women should not be allowed to vote, this is a...      1

[5003 rows x 2 columns]

In [9]:
# PREPROCESSING
# Need more preprocessing :
#  - stopwords : Name, URL

# Worst 10%
# df = df.loc[df.hate_speech_score > df.hate_speech_score.quantile(0.90)]

# Get negative examples
# n = 12785 # = number of gathered worst examples
# df = df.loc[df.hate_speech_score < df.hate_speech_score.quantile(0.1)].iloc[:n]


0         2.0
1         2.0
2         4.0
3         2.0
4         4.0
         ... 
135551    2.0
135552    2.0
135553    1.0
135554    2.0
135555    2.0
Name: status, Length: 135556, dtype: float64

#### Language detection

In [21]:
# Language detection model
tokenizer = AutoTokenizer.from_pretrained("papluca/xlm-roberta-base-language-detection")
model = XLMRobertaForSequenceClassification.from_pretrained("papluca/xlm-roberta-base-language-detection").to("cuda")

In [59]:
# Add language prediction for later filtering before applying language-dependent translation model
df["lang"] = df.text.progress_apply(lambda text: detect_language(model, tokenizer, text))

100%|████████████████████████████████████████████████████████████████████████████████████████████| 135556/135556 [18:54<00:00, 119.45it/s]


#### Text translation

- Process requires long processing time
- Process should be run multiple times to complete

In [19]:
! rm -rf temp/*

zsh:1: no matches found: temp/*


In [25]:
def write_file(path, text):
    with open(path, "w") as f:
        f.write(text)

LANGUAGE = "en"
OUTPUT_DIR = "../data/translated"
TEMP_DIR = "../data/temp"
IN_MEMORY = True

output_dir = os.path.join(OUTPUT_DIR, LANGUAGE)
if not os.path.exists(OUTPUT_DIR):
    os.makedirs(output_dir)
#     os.mkdir(OUTPUT_DIR)
if not os.path.exists(TEMP_DIR):
    os.mkdir(TEMP_DIR)

In [7]:
# Translation model
tokenizer = AutoTokenizer.from_pretrained("Abelll/marian-finetuned-kde4-en-to-fr")
model = MarianMTModel.from_pretrained("Abelll/marian-finetuned-kde4-en-to-fr").to("cuda")

In [26]:
translated_texts = []
for i, row in tqdm(df.iterrows(), total=df.shape[0]):
    output_path = os.path.join(TEMP_DIR, str(i) + ".txt")
    if not IN_MEMORY:
        if os.path.exists(output_path):
            print("Already translated !")
            continue
    translated = translate(model, tokenizer, row.text)
    if IN_MEMORY:
        translated_texts.append((i, translated))
    else:
        write_file(output_path, translated)

  0%|                                                                                              | 0/5003 [00:00<?, ?it/s]/home/louis/miniconda3/envs/sexism_detection/lib/python3.9/site-packages/transformers/generation/utils.py:1387: UserWarning: Neither `max_length` nor `max_new_tokens` has been set, `max_length` will default to 512 (`self.config.max_length`). Controlling `max_length` via the config is deprecated and `max_length` will be removed from the config in v5 of Transformers -- we recommend using `max_new_tokens` to control the maximum length of the generation.
  warnings.warn(
100%|███████████████████████████████████████████████████████████████████████████████████| 5003/5003 [10:27<00:00,  7.97it/s]


In [29]:
import glob

output_filename = DATASET_PATH

if not IN_MEMORY:
    filelist = glob.glob(TEMP_DIR + "/*")
    print(f"Found {len(filelist)}")
    filelist = sorted(filelist, key=lambda x: int(x.split("/")[-1].split(".")[0]))
    translated_texts = []
    for text_file in tqdm(filelist):
        with open(text_file) as f:
            translated_text = f.read().splitlines()
        translated_texts.append(translated_text)
    translated_texts = pd.DataFrame(translated_texts)
    df["translated"] = translated_texts

df["translated"] = translated_texts
df.translated = df.translated.apply(lambda x: x[1])
df.dropna().to_csv(output_filename)

In [30]:
df

text  label  \
INDEX                                                             
0      Maybe the UN could talk to those asian and afr...      1   
1      ‘Juice (Jews) are worse that nukes.’ Caption t...      1   
2      Foreigners on UK benefits leaps 41% in 5 years...      1   
3      Jews cannot be patriots, since their allegianc...      1   
4      Israel, Zionism and Jewish Supremacist control...      1   
...                                                  ...    ...   
4998                      Woman are basically childlike.      1   
4999                  women should be submissive to men.      1   
5000   Women are essentially childlike, unable to und...      1   
5001                  Women should be submissive to men.      1   
5002   Women should not be allowed to vote, this is a...      1   

                                              translated  
INDEX                                                     
0      Peut-être que l'Onu pourrait parler aux nation...  
1      « Juice (Juifs) sont pire que les nuées. « & #...  
2      Les étrangers au Royaume-Uni bénéficient d'un ...  
3      Les Juifs ne peuvent pas être patriotes, car l...  
4      Israël, le sionisme et le contrôle suprémacist...  
...                                                  ...  
4998                     La femme ressemble à un enfant.  
4999        Les filles doivent être soumises aux hommes.  
5000   Les filles sont pour l'essentiel des filles, i...  
5001        Les filles doivent être soumises aux hommes.  
5002   Les femmes ne devraient pas être autorisées à ...  

[5003 rows x 3 columns]

In [12]:
df.to_csv("../data/ucberkeley-dlab_measuring-hate-speech_translated_positive.csv")

In [65]:
def translate(text):
    input_text = f"translate {BASE_LANGUAGE} to French: " + text.lower()
    print(input_text)
    input_ids = tokenizer(input_text, return_tensors="pt").input_ids
    outputs = model.generate(input_ids)
    decoded = tokenizer.decode(outputs[0], skip_special_tokens=True)
    return decoded

translate(df.text[4])

translate English to French: for starters bend over the one in pink and kick that ass and pussy to get a taste until she's begging for a dick inside her.


"j'ai lu cette vidéo et j'ai"

In [8]:
model

MarianMTModel(
  (model): MarianModel(
    (shared): Embedding(59514, 512, padding_idx=59513)
    (encoder): MarianEncoder(
      (embed_tokens): Embedding(59514, 512, padding_idx=59513)
      (embed_positions): MarianSinusoidalPositionalEmbedding(512, 512)
      (layers): ModuleList(
        (0): MarianEncoderLayer(
          (self_attn): MarianAttention(
            (k_proj): Linear(in_features=512, out_features=512, bias=True)
            (v_proj): Linear(in_features=512, out_features=512, bias=True)
            (q_proj): Linear(in_features=512, out_features=512, bias=True)
            (out_proj): Linear(in_features=512, out_features=512, bias=True)
          )
          (self_attn_layer_norm): LayerNorm((512,), eps=1e-05, elementwise_affine=True)
          (activation_fn): SiLUActivation()
          (fc1): Linear(in_features=512, out_features=2048, bias=True)
          (fc2): Linear(in_features=2048, out_features=512, bias=True)
          (final_layer_norm): LayerNorm((512,), eps=1